In [341]:
import sys, os
sys.path.append(os.path.join(os.getcwd(), '..'))
sys.path.append(os.path.join(os.getcwd(), '..', '..'))
sys.path.append(os.path.join(os.getcwd(), '..', '..', '..', 'pplSIT', 'workflow', 'utils'))

In [342]:
%matplotlib inline

from session.sessions import selected_009266, selected_008229, selected_009265
from imports import *
from scipy import stats
from scipy import signal
from target import get_spike_counts
from Behavior.behavior import get_idxs_neuro_state, get_idxs_behav_state
from population import unit_response_matrix, activity_at_phase

In [343]:
%%javascript
IPython.OutputArea.prototype._should_scroll = function(lines) {
    return false;
}

<IPython.core.display.Javascript object>

In [344]:
def get_positions_relative_to(pos_alo, HD, poi, res_type='polar'):
    """
    pos_alo     2D array of allocentric animal positions X, Y  (shape Nx2)
    HD          vector of HD angles (in rad.) for each pos_alo (shape N)
    poi         point of interest (x, y) relative to which to compute egocentric coords.
    """
    pos_poi = poi - pos_alo
    R = np.linalg.norm(pos_poi, axis=1)  # distance from animal to the POI
    phi_alo = (np.degrees(np.arctan2(pos_poi[:, 1], pos_poi[:, 0])) - HD) % 360  # angle to POI in allocentric frame, in deg.
    phi_ego = phi_alo - np.rad2deg(HD)  # angle to POI in egocentric frame, in deg.
    phi_ego = np.deg2rad(phi_ego)
    
    if res_type == 'polar':
        return np.array([R, phi_ego]).T
    return np.array([np.multiply(R, np.cos(phi_ego)), np.multiply(R, np.sin(phi_ego))]).T

In [345]:
source = '/home/sobolev/nevermind_ag-grothe/AG_Pecka/data/processed/'
source = '/home/sobolev/nevermind/AG_Pecka/data/processed/'

sessions = [s for s in selected_009266.keys()]
sessions = [s for s in selected_009265.keys()]
#sessions = [s for s in selected_008229.keys()]
sessions.sort()

try:
    sessions.remove('009266_hippoSIT_2023-04-20_15-24-14')
except:
    pass
try:
    sessions.remove('009265_hippoSIT_2023-02-27_10-18-32')
    sessions.remove('009265_hippoSIT_2023-02-27_15-33-46')
except:
    pass

# special for 009265
sessions = sessions[7:-1]
sessions

['009265_hippoSIT_2023-03-02_16-27-42',
 '009265_hippoSIT_2023-03-02_20-11-35',
 '009265_hippoSIT_2023-03-03_09-37-07',
 '009265_hippoSIT_2023-03-03_16-00-47',
 '009265_hippoSIT_2023-03-04_11-12-04',
 '009265_hippoSIT_2023-03-05_11-52-17',
 '009265_hippoSIT_2023-03-05_18-31-32',
 '009265_hippoSIT_2023-03-08_18-10-07',
 '009265_hippoSIT_2023-03-09_20-03-08',
 '009265_hippoSIT_2023-03-10_09-57-34',
 '009265_hippoSIT_2023-04-13_09-54-39']

In [346]:
# '009265_hippoSIT_2023-03-08_18-10-07'
# quite some cells azimuthally tuned to the working speaker at W1
# at the same time W4 is anti-tuned to W1 (which makes sense)
# however all cells at W1 are tuned to the speaker at ~90deg. 
# Which is weird. So maybe all is an artifact

session = sessions[7]
session

'009265_hippoSIT_2023-03-08_18-10-07'

In [347]:
ft = 'tSNE'
fp = 70
#ft = 'UMAP'
#fp = '0.7'
speed_thresh = 0.05  # m/s

animal = session.split('_')[0]

s_path     = os.path.join(source, animal, session)
meta_file  = os.path.join(source, animal, session, 'meta.h5')
moseq_file = os.path.join(source, animal, session, 'MoSeq.h5')
desc_file  = os.path.join(source, animal, session, 'descendants.h5')
umap_file  = os.path.join(source, animal, session, 'analysis', 'W1-W4_tSNE_UMAP.h5')
units_file = os.path.join(source, animal, session, 'units.h5')

with h5py.File(meta_file, 'r') as f:
    tl = np.array(f['processed']['timeline'])
    tgt_mx = np.array(f['processed']['target_matrix'])
    events = np.array(f['processed']['sound_events'])
    cfg = json.loads(f['processed'].attrs['parameters'])
with h5py.File(umap_file, 'r') as f:
    fit = np.array(f[ft][str(fp)])
with h5py.File(moseq_file, 'r') as f:
    moseq = np.array(f['moseq'])
with h5py.File(desc_file, 'r') as f:
    speed = np.array(f['speed'])
    hd    = np.array(f['hd'])
unit_names, single_units, spike_times = [], {}, {}
with h5py.File(units_file, 'r') as f:
    unit_names = [x for x in f]
with h5py.File(units_file, 'r') as f:
    for unit_name in unit_names:
        spike_times[unit_name] = np.array(f[unit_name][H5NAMES.spike_times['name']])
        single_units[unit_name] = np.array(f[unit_name][H5NAMES.inst_rate['name']])

In [348]:
# auditory state (BGR, SIL etc.) and speed filter
idxs_idle_ev = np.where(speed[events[:, 2].astype(np.int32)] < speed_thresh)[0]  # define speed filter here
idxs_bgr_ev  = np.where(events[:, 1] == 1)[0]
idxs_sil_ev  = np.where(events[:, 1] == 0)[0]
idxs_tgt_ev  = np.where(events[:, 1] == 2)[0]
idxs_tri_ev  = np.where( (events[:, 1] == 1) | (events[:, 1] == 2) )[0]  # in the trial

# behavioral state
idxs_tl_tgt_succ = []
idxs_tl_pellet   = []
idxs_tgt_succ_ev = []
for tgt_rec in tgt_mx[tgt_mx[:, 4] == 1]:
    idxs_tl_tgt_succ += list(range(tgt_rec[2], tgt_rec[3]))
    idxs_tl_pellet   += list(range(tgt_rec[3] + 1*100, tgt_rec[3] + 6*100))
    idxs_tgt_succ_ev += list(range(tgt_rec[0], tgt_rec[1]))
idxs_tl_tgt_succ = np.array(idxs_tl_tgt_succ)
idxs_tl_pellet   = np.array(idxs_tl_pellet)

idxs_AL_tl = get_idxs_behav_state(source, session, idxs_tl_tgt_succ, fit_type=ft, fit_parm=fp, sigma=0.3, margin=10, bin_count=100)
idxs_PC_tl = get_idxs_behav_state(source, session, idxs_tl_pellet, fit_type=ft, fit_parm=fp, sigma=0.3, margin=10, bin_count=100)

idxs_AL_ev = np.array([k for k, x in enumerate(events) if x[2] in idxs_AL_tl], dtype=np.int32)
idxs_PC_ev = np.array([k for k, x in enumerate(events) if x[2] in idxs_PC_tl], dtype=np.int32)

# final separation
idxs_AL_bgr_ev  = np.intersect1d(idxs_AL_ev, idxs_bgr_ev)
idxs_AL_tgt_ev  = np.intersect1d(idxs_AL_ev, idxs_tgt_ev)
idxs_AL_sil_ev  = np.intersect1d(idxs_AL_ev, idxs_sil_ev)

idxs_PH_ev = np.array([x for x in range(len(events)) if not x in idxs_AL_ev])
idxs_PH_bgr_ev = np.intersect1d(idxs_PH_ev, idxs_bgr_ev)
idxs_PH_sil_ev = np.intersect1d(idxs_PH_ev, idxs_sil_ev)

idxs_AL_bgr_rest_ev = np.intersect1d(idxs_AL_bgr_ev, idxs_idle_ev)
idxs_PH_bgr_rest_ev = np.intersect1d(idxs_PH_bgr_ev, idxs_idle_ev)
idxs_AL_sil_rest_ev = np.intersect1d(idxs_AL_sil_ev, idxs_idle_ev)
idxs_PH_sil_rest_ev = np.intersect1d(idxs_PH_sil_ev, idxs_idle_ev)

print(len(idxs_AL_bgr_rest_ev), len(idxs_PH_bgr_rest_ev))
print(len(idxs_AL_sil_rest_ev), len(idxs_PH_sil_rest_ev))
print(len(idxs_tgt_succ_ev))

899 1356
462 786
669


In [349]:
times_to_event = [15, 28, 73, 100]
bins_umx, unit_mx = unit_response_matrix(s_path, range(10), times_to_event=times_to_event)

In [350]:
speaker_N  = np.array((0, 0.5))  # this one is used for BGR most of the time
speaker_SW = np.array((-0.37, -0.37))
door       = np.array((0.5, 0))

segments = 12
to_plot = [name for name in unit_names if int(name[0]) < 13][:]
colors = ['green', 'black', 'red']
circ_bins = np.linspace(-np.pi, np.pi, segments+1)
bins_to_plot = np.linspace(-360, 360, 2*segments)
cols = 4
rows = len(to_plot)
fig, axes = plt.subplots(rows, cols, figsize=(cols*4, rows*4))

for i, unit_name in enumerate(to_plot):
    for phase in np.arange(4) + 1:
        unit_all = unit_mx[:, i]  # unevenly binned spiketrain of the selected unit i
        resp_at_phase = unit_all[phase::len(times_to_event) + 1]  # response of that unit at phase (number of spikes)
        
        ax = axes[i][phase-1]
        ax.grid(axis='y')
        if phase == 1:
            ax.set_ylabel('%s, spike count' % unit_name, fontsize=14)
        if i == 0:
            ax.set_title("W%d" % phase, fontsize=14)
                
        for j, idxs in enumerate([idxs_AL_bgr_rest_ev, idxs_PH_bgr_rest_ev, idxs_tgt_succ_ev]):
            tl_idxs = events[idxs][:, 2].astype(np.int32)
            
            # convert relative to the speaker!
            speaker = speaker_N if j < 2 else speaker_SW
            resp_AL    = resp_at_phase[idxs]  # event sampling
            hd_Al      = hd[tl_idxs]
            pos_AL_alo = tl[:, 1:3][tl_idxs]
            pos_AL_ego = get_positions_relative_to(pos_AL_alo, hd_Al, speaker)  # in polar coord.
            phi_AL = pos_AL_ego[:, 1]
            phi_AL[np.where(phi_AL > np.pi)[0]] -= 2*np.pi
            
            assert (phi_AL > -np.pi).all()
            assert (phi_AL < np.pi).all()
            
            # regular bins
#             circ_hist = np.zeros(len(circ_bins) - 1)
#             for k in range(len(circ_bins) - 1):
#                 idxs_hd = np.where( (phi_AL > circ_bins[k]) & (phi_AL < circ_bins[k+1]) )[0]
#                 if len(idxs_hd) > 0:
#                     circ_hist[k] = resp_AL[idxs_hd].mean()
#             collected = circ_hist
            
            # do binning in steps
            bin_l = 2*np.pi/segments
            iter_count = 6
            collected = []
            for z in range(iter_count):
                step = bin_l/iter_count  # all in radians
                circ_hist = np.zeros(len(circ_bins) - 1)
                for k in range(len(circ_bins) - 2):
                    idxs_hd = np.where( (phi_AL > circ_bins[k] + z*step) & (phi_AL < circ_bins[k+1] + z*step) )[0]
                    if len(idxs_hd) > 0:
                        circ_hist[k] = resp_AL[idxs_hd].mean()
                # compensate last bin
                k = len(circ_bins) - 2
                idxs_hd_1 = np.where( (phi_AL > -np.pi) & (phi_AL < circ_bins[0] + z*step) )[0]
                idxs_hd_2 = np.where( (phi_AL > circ_bins[k] + z*step) & (phi_AL < circ_bins[k+1] + z*step) )[0]
                idxs_both = np.union1d(idxs_hd_1, idxs_hd_2)
                if len(idxs_both) > 0:
                    circ_hist[-1] += resp_AL[idxs_both].mean()
                    
                collected.append(circ_hist)
            collected = np.array(collected)
            collected = collected.mean(axis=0)

            ax.plot(bins_to_plot, np.concatenate([collected, collected]), color=colors[j])

### Check up target / background speaker location

In [351]:
#if False:
for session in sessions:
    animal = session.split('_')[0]

    s_path     = os.path.join(source, animal, session)
    meta_file  = os.path.join(source, animal, session, 'meta.h5')

    with h5py.File(meta_file, 'r') as f:
        cfg = json.loads(f['processed'].attrs['parameters'])

    ch_tgt = cfg['sound']['sounds']['target']['channels']
    ch_bgr = cfg['sound']['sounds']['background']['channels']
    print("TGT: %s, BGR: %s" % (str(ch_tgt), str(ch_bgr)))

TGT: [3, 8], BGR: [1, 8]
TGT: [3, 8], BGR: [1, 8]
TGT: [3, 8], BGR: [1, 8]
TGT: [3, 8], BGR: [1, 8]
TGT: [3, 8], BGR: [1, 8]
TGT: [3, 8], BGR: [1, 8]
TGT: [3, 8], BGR: [1, 8]
TGT: [3, 8], BGR: [1, 8]
TGT: [3, 8], BGR: [1, 8]
TGT: [3, 8], BGR: [1, 8]
TGT: [5], BGR: [3]
